In [1]:
import argparse
import numpy as np
from driver_base import FINNExampleOverlay
from qonnx.core.datatype import DataType
import os
import platform
import pynq

In [2]:
def get_edge_or_pcie():
    cpu = platform.processor()
    if cpu in ["armv7l", "aarch64"]:
        return "edge"
    elif cpu in ["x86_64"]:
        return "pcie"
    else:
        raise OSError("Platform is not supported.")

In [3]:
# parse arguments
bitfile = "../bitfile/finn-accel.bit"
from driver import io_shape_dict
driver_modes = {"edge": "zynq-iodma", "pcie": "alveo"}
target_platform = pynq.Device.active_device.name
driver_mode = driver_modes[get_edge_or_pcie()]

In [4]:
def normalize_array(arr):

  # find the minimum and maximum values in the array.
  min_val = -2
  max_val = 2

  normalized_arr = 256 * (arr - min_val) / (max_val - min_val) - 128

  return normalized_arr

In [10]:
folder = "/home/xilinx/jupyter_notebooks/data"

files = os.listdir(folder)

filtered_files = files

filtered_files.remove('.ipynb_checkpoints')

factor = 1
noFiles = len(filtered_files)

arr = np.ndarray((int(7800*noFiles/factor),1,128*factor*2), float)
labels = np.ndarray((int(7800*noFiles/factor),4))

seed = 42

i = 0;
for idx, npz in enumerate(filtered_files):
    
    a = np.load(os.path.join(folder, npz))
    
    start_idx = (idx*int(7800/factor)) if idx <20 else (idx)*int(7800/factor)-1
    end_idx = (1+idx)*int(7800/factor) if idx <20 else (1+idx)*int(7800/factor)-1
    
    # print(f"start index: {start_idx}, end index {end_idx}, activate channels: {a['active_channels']}")
       
    reshaped_arr = a["samples"].reshape(int(7800/factor),1, 128*factor)
    
    float_array = np.concatenate((reshaped_arr.real, reshaped_arr.imag), axis=2)
    
    #float_array = float_array.reshape(int(7800/factor), 128*factor,1,2)

    arr[start_idx:end_idx] = float_array
    labels[start_idx:end_idx] = np.tile(a["active_channels"],  (int(7800/factor), 1))

    i+=1
    if i >= noFiles:
        break
    
normalized_array = normalize_array(arr)
labels = labels


print(f"Original array min: {np.min(arr)}, max: {np.max(arr)}")
print(f"Normalized array min: {np.min(normalized_array)}, max: {np.max(normalized_array)}")

Original array min: -1.972787847664288, max: 1.9611613513818402
Normalized array min: -126.25842225051443, max: 125.51432648843777


In [11]:
driver = FINNExampleOverlay(bitfile, driver_mode, io_shape_dict,fclk_mhz = 10.0)

In [12]:
print(normalized_array.shape)

(85800, 1, 256)


In [13]:
test_single = normalized_array[-20].astype(np.int8)
test_single_label = labels[-1].astype(np.float32)

print(test_single.shape)
print(test_single_label)


(1, 256)
[1. 0. 0. 0.]


In [14]:
accel_out = driver.execute(test_single)

In [15]:
print(accel_out)

[[-1. -1. -1. -1.]]


In [ ]:
batch_size = 1
driver.batch_size = batch_size
(test_imgs, test_labels) = (normalized_array.astype(np.int8),labels)

ok = 0
nok = 0
n_batches = test_imgs.shape[0]
total = batch_size*n_batches

for i in range(n_batches):
    inp = test_imgs[i]
    exp = test_labels[i].astype(np.float32)
    out = driver.execute(inp)
    out = [(x+1)/2 for x in out]
    ok += 1 if (out==exp).all() else 0
    nok += 1 if (out != exp).any() else 0
    print("batch %d / %d : total OK %d NOK %d" % (i + 1, n_batches, ok, nok))

acc = 100.0 * ok / (ok+nok)
print("Final accuracy: {:.2f}%".format(acc))

def run_validation():
    for i in range(n_batches):
        ibuf_normal = test_imgs[i].reshape(driver.ishape_normal())
        driver.execute(ibuf_normal)

full_validation_time = %timeit -n 1 -o run_validation()



batch 1 / 85800 : total OK 1 NOK 0
batch 2 / 85800 : total OK 2 NOK 0
batch 3 / 85800 : total OK 2 NOK 1
batch 4 / 85800 : total OK 2 NOK 2
batch 5 / 85800 : total OK 3 NOK 2
batch 6 / 85800 : total OK 4 NOK 2
batch 7 / 85800 : total OK 5 NOK 2
batch 8 / 85800 : total OK 5 NOK 3
batch 9 / 85800 : total OK 5 NOK 4
batch 10 / 85800 : total OK 5 NOK 5
batch 11 / 85800 : total OK 5 NOK 6
batch 12 / 85800 : total OK 6 NOK 6
batch 13 / 85800 : total OK 7 NOK 6
batch 14 / 85800 : total OK 7 NOK 7
batch 15 / 85800 : total OK 8 NOK 7
batch 16 / 85800 : total OK 9 NOK 7
batch 17 / 85800 : total OK 10 NOK 7
batch 18 / 85800 : total OK 10 NOK 8
batch 19 / 85800 : total OK 11 NOK 8
batch 20 / 85800 : total OK 12 NOK 8
batch 21 / 85800 : total OK 12 NOK 9
batch 22 / 85800 : total OK 13 NOK 9
batch 23 / 85800 : total OK 13 NOK 10
batch 24 / 85800 : total OK 13 NOK 11
batch 25 / 85800 : total OK 14 NOK 11
batch 26 / 85800 : total OK 14 NOK 12
batch 27 / 85800 : total OK 15 NOK 12
batch 28 / 85800 : to

batch 241 / 85800 : total OK 92 NOK 149
batch 242 / 85800 : total OK 92 NOK 150
batch 243 / 85800 : total OK 92 NOK 151
batch 244 / 85800 : total OK 92 NOK 152
batch 245 / 85800 : total OK 93 NOK 152
batch 246 / 85800 : total OK 93 NOK 153
batch 247 / 85800 : total OK 94 NOK 153
batch 248 / 85800 : total OK 95 NOK 153
batch 249 / 85800 : total OK 95 NOK 154
batch 250 / 85800 : total OK 95 NOK 155
batch 251 / 85800 : total OK 95 NOK 156
batch 252 / 85800 : total OK 95 NOK 157
batch 253 / 85800 : total OK 95 NOK 158
batch 254 / 85800 : total OK 96 NOK 158
batch 255 / 85800 : total OK 96 NOK 159
batch 256 / 85800 : total OK 97 NOK 159
batch 257 / 85800 : total OK 98 NOK 159
batch 258 / 85800 : total OK 98 NOK 160
batch 259 / 85800 : total OK 99 NOK 160
batch 260 / 85800 : total OK 99 NOK 161
batch 261 / 85800 : total OK 99 NOK 162
batch 262 / 85800 : total OK 100 NOK 162
batch 263 / 85800 : total OK 100 NOK 163
batch 264 / 85800 : total OK 100 NOK 164
batch 265 / 85800 : total OK 100 NOK 

batch 483 / 85800 : total OK 193 NOK 290
batch 484 / 85800 : total OK 193 NOK 291
batch 485 / 85800 : total OK 193 NOK 292
batch 486 / 85800 : total OK 193 NOK 293
batch 487 / 85800 : total OK 193 NOK 294
batch 488 / 85800 : total OK 193 NOK 295
batch 489 / 85800 : total OK 193 NOK 296
batch 490 / 85800 : total OK 193 NOK 297
batch 491 / 85800 : total OK 193 NOK 298
batch 492 / 85800 : total OK 193 NOK 299
batch 493 / 85800 : total OK 193 NOK 300
batch 494 / 85800 : total OK 194 NOK 300
batch 495 / 85800 : total OK 194 NOK 301
batch 496 / 85800 : total OK 195 NOK 301
batch 497 / 85800 : total OK 195 NOK 302
batch 498 / 85800 : total OK 196 NOK 302
batch 499 / 85800 : total OK 197 NOK 302
batch 500 / 85800 : total OK 197 NOK 303
batch 501 / 85800 : total OK 198 NOK 303
batch 502 / 85800 : total OK 199 NOK 303
batch 503 / 85800 : total OK 200 NOK 303
batch 504 / 85800 : total OK 201 NOK 303
batch 505 / 85800 : total OK 202 NOK 303
batch 506 / 85800 : total OK 202 NOK 304
batch 507 / 8580

batch 724 / 85800 : total OK 282 NOK 442
batch 725 / 85800 : total OK 282 NOK 443
batch 726 / 85800 : total OK 282 NOK 444
batch 727 / 85800 : total OK 283 NOK 444
batch 728 / 85800 : total OK 284 NOK 444
batch 729 / 85800 : total OK 285 NOK 444
batch 730 / 85800 : total OK 286 NOK 444
batch 731 / 85800 : total OK 287 NOK 444
batch 732 / 85800 : total OK 288 NOK 444
batch 733 / 85800 : total OK 288 NOK 445
batch 734 / 85800 : total OK 288 NOK 446
batch 735 / 85800 : total OK 289 NOK 446
batch 736 / 85800 : total OK 290 NOK 446
batch 737 / 85800 : total OK 290 NOK 447
batch 738 / 85800 : total OK 290 NOK 448
batch 739 / 85800 : total OK 291 NOK 448
batch 740 / 85800 : total OK 292 NOK 448
batch 741 / 85800 : total OK 292 NOK 449
batch 742 / 85800 : total OK 292 NOK 450
batch 743 / 85800 : total OK 293 NOK 450
batch 744 / 85800 : total OK 294 NOK 450
batch 745 / 85800 : total OK 294 NOK 451
batch 746 / 85800 : total OK 295 NOK 451
batch 747 / 85800 : total OK 296 NOK 451
batch 748 / 8580

batch 925 / 85800 : total OK 374 NOK 551
batch 926 / 85800 : total OK 375 NOK 551
batch 927 / 85800 : total OK 375 NOK 552
batch 928 / 85800 : total OK 376 NOK 552
batch 929 / 85800 : total OK 376 NOK 553
batch 930 / 85800 : total OK 376 NOK 554
batch 931 / 85800 : total OK 376 NOK 555
batch 932 / 85800 : total OK 377 NOK 555
batch 933 / 85800 : total OK 377 NOK 556
batch 934 / 85800 : total OK 377 NOK 557
batch 935 / 85800 : total OK 377 NOK 558
batch 936 / 85800 : total OK 377 NOK 559
batch 937 / 85800 : total OK 377 NOK 560
batch 938 / 85800 : total OK 377 NOK 561
batch 939 / 85800 : total OK 377 NOK 562
batch 940 / 85800 : total OK 377 NOK 563
batch 941 / 85800 : total OK 377 NOK 564
batch 942 / 85800 : total OK 377 NOK 565
batch 943 / 85800 : total OK 378 NOK 565
batch 944 / 85800 : total OK 378 NOK 566
batch 945 / 85800 : total OK 379 NOK 566
batch 946 / 85800 : total OK 380 NOK 566
batch 947 / 85800 : total OK 380 NOK 567
batch 948 / 85800 : total OK 381 NOK 567
batch 949 / 8580

...

batch 84849 / 85800 : total OK 40138 NOK 44711
batch 84850 / 85800 : total OK 40138 NOK 44712
batch 84851 / 85800 : total OK 40139 NOK 44712
batch 84852 / 85800 : total OK 40140 NOK 44712
batch 84853 / 85800 : total OK 40140 NOK 44713
batch 84854 / 85800 : total OK 40140 NOK 44714
batch 84855 / 85800 : total OK 40140 NOK 44715
batch 84856 / 85800 : total OK 40141 NOK 44715
batch 84857 / 85800 : total OK 40141 NOK 44716
batch 84858 / 85800 : total OK 40141 NOK 44717
batch 84859 / 85800 : total OK 40142 NOK 44717
batch 84860 / 85800 : total OK 40142 NOK 44718
batch 84861 / 85800 : total OK 40142 NOK 44719
batch 84862 / 85800 : total OK 40142 NOK 44720
batch 84863 / 85800 : total OK 40142 NOK 44721
batch 84864 / 85800 : total OK 40142 NOK 44722
batch 84865 / 85800 : total OK 40143 NOK 44722
batch 84866 / 85800 : total OK 40144 NOK 44722
batch 84867 / 85800 : total OK 40145 NOK 44722
batch 84868 / 85800 : total OK 40145 NOK 44723
batch 84869 / 85800 : total OK 40145 NOK 44724
batch 84870 /

batch 85043 / 85800 : total OK 40172 NOK 44871
batch 85044 / 85800 : total OK 40172 NOK 44872
batch 85045 / 85800 : total OK 40172 NOK 44873
batch 85046 / 85800 : total OK 40172 NOK 44874
batch 85047 / 85800 : total OK 40172 NOK 44875
batch 85048 / 85800 : total OK 40172 NOK 44876
batch 85049 / 85800 : total OK 40173 NOK 44876
batch 85050 / 85800 : total OK 40174 NOK 44876
batch 85051 / 85800 : total OK 40175 NOK 44876
batch 85052 / 85800 : total OK 40175 NOK 44877
batch 85053 / 85800 : total OK 40175 NOK 44878
batch 85054 / 85800 : total OK 40176 NOK 44878
batch 85055 / 85800 : total OK 40176 NOK 44879
batch 85056 / 85800 : total OK 40176 NOK 44880
batch 85057 / 85800 : total OK 40176 NOK 44881
batch 85058 / 85800 : total OK 40177 NOK 44881
batch 85059 / 85800 : total OK 40178 NOK 44881
batch 85060 / 85800 : total OK 40178 NOK 44882
batch 85061 / 85800 : total OK 40178 NOK 44883
batch 85062 / 85800 : total OK 40178 NOK 44884
batch 85063 / 85800 : total OK 40178 NOK 44885
batch 85064 /

batch 85237 / 85800 : total OK 40210 NOK 45027
batch 85238 / 85800 : total OK 40210 NOK 45028
batch 85239 / 85800 : total OK 40210 NOK 45029
batch 85240 / 85800 : total OK 40210 NOK 45030
batch 85241 / 85800 : total OK 40210 NOK 45031
batch 85242 / 85800 : total OK 40210 NOK 45032
batch 85243 / 85800 : total OK 40210 NOK 45033
batch 85244 / 85800 : total OK 40210 NOK 45034
batch 85245 / 85800 : total OK 40210 NOK 45035
batch 85246 / 85800 : total OK 40210 NOK 45036
batch 85247 / 85800 : total OK 40210 NOK 45037
batch 85248 / 85800 : total OK 40210 NOK 45038
batch 85249 / 85800 : total OK 40210 NOK 45039
batch 85250 / 85800 : total OK 40210 NOK 45040
batch 85251 / 85800 : total OK 40210 NOK 45041
batch 85252 / 85800 : total OK 40211 NOK 45041
batch 85253 / 85800 : total OK 40211 NOK 45042
batch 85254 / 85800 : total OK 40211 NOK 45043
batch 85255 / 85800 : total OK 40211 NOK 45044
batch 85256 / 85800 : total OK 40211 NOK 45045
batch 85257 / 85800 : total OK 40211 NOK 45046
batch 85258 /

batch 85437 / 85800 : total OK 40246 NOK 45191
batch 85438 / 85800 : total OK 40246 NOK 45192
batch 85439 / 85800 : total OK 40246 NOK 45193
batch 85440 / 85800 : total OK 40246 NOK 45194
batch 85441 / 85800 : total OK 40247 NOK 45194
batch 85442 / 85800 : total OK 40247 NOK 45195
batch 85443 / 85800 : total OK 40247 NOK 45196
batch 85444 / 85800 : total OK 40247 NOK 45197
batch 85445 / 85800 : total OK 40248 NOK 45197
batch 85446 / 85800 : total OK 40248 NOK 45198
batch 85447 / 85800 : total OK 40248 NOK 45199
batch 85448 / 85800 : total OK 40248 NOK 45200
batch 85449 / 85800 : total OK 40248 NOK 45201
batch 85450 / 85800 : total OK 40248 NOK 45202
batch 85451 / 85800 : total OK 40248 NOK 45203
batch 85452 / 85800 : total OK 40248 NOK 45204
batch 85453 / 85800 : total OK 40248 NOK 45205
batch 85454 / 85800 : total OK 40248 NOK 45206
batch 85455 / 85800 : total OK 40249 NOK 45206
batch 85456 / 85800 : total OK 40249 NOK 45207
batch 85457 / 85800 : total OK 40249 NOK 45208
batch 85458 /

batch 85634 / 85800 : total OK 40284 NOK 45350
batch 85635 / 85800 : total OK 40284 NOK 45351
batch 85636 / 85800 : total OK 40284 NOK 45352
batch 85637 / 85800 : total OK 40284 NOK 45353
batch 85638 / 85800 : total OK 40284 NOK 45354
batch 85639 / 85800 : total OK 40285 NOK 45354
batch 85640 / 85800 : total OK 40285 NOK 45355
batch 85641 / 85800 : total OK 40286 NOK 45355
batch 85642 / 85800 : total OK 40286 NOK 45356
batch 85643 / 85800 : total OK 40286 NOK 45357
batch 85644 / 85800 : total OK 40286 NOK 45358
batch 85645 / 85800 : total OK 40286 NOK 45359
batch 85646 / 85800 : total OK 40286 NOK 45360
batch 85647 / 85800 : total OK 40286 NOK 45361
batch 85648 / 85800 : total OK 40287 NOK 45361
batch 85649 / 85800 : total OK 40287 NOK 45362
batch 85650 / 85800 : total OK 40287 NOK 45363
batch 85651 / 85800 : total OK 40287 NOK 45364
batch 85652 / 85800 : total OK 40287 NOK 45365
batch 85653 / 85800 : total OK 40287 NOK 45366
batch 85654 / 85800 : total OK 40287 NOK 45367
batch 85655 /